In [1]:
import cv2
from pathlib import Path
import numpy as np
from tqdm.autonotebook import tqdm
from trap.frame_emitter import DetectionState, Frame, Detection, Track
from collections.abc import Iterable

/tmp/ipykernel_1756367/2768163695.py:4: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm


In [2]:
video_srcs = list(Path('../DATASETS/hof/').glob('*.m4v'))

video_srcs

[PosixPath('../DATASETS/hof/webcam20240110-4.m4v'),
 PosixPath('../DATASETS/hof/webcam20231103-4.m4v'),
 PosixPath('../DATASETS/hof/webcam20231103-2.m4v'),
 PosixPath('../DATASETS/hof/webcam20231103-3.m4v'),
 PosixPath('../DATASETS/hof/webcam20240110-2.m4v'),
 PosixPath('../DATASETS/hof/webcam20240111-2.m4v'),
 PosixPath('../DATASETS/hof/webcam20240111-1.m4v'),
 PosixPath('../DATASETS/hof/webcam20240110-3.m4v'),
 PosixPath('../DATASETS/hof/webcam20240110-1.m4v'),
 PosixPath('../DATASETS/hof/webcam20240111-3.m4v')]

In [3]:
import torch


device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [4]:
import collections
from torchvision.models.detection import maskrcnn_resnet50_fpn_v2, MaskRCNN_ResNet50_FPN_V2_Weights, KeypointRCNN_ResNet50_FPN_Weights, keypointrcnn_resnet50_fpn
from deep_sort_realtime.deepsort_tracker import DeepSort
from ultralytics import YOLO
from ultralytics.engine.results import Results as YOLOResult

def tracker(frame_generator: collections.abc.Iterable[Frame]) -> collections.abc.Iterable[Frame]:
    first_frame: Frame = frame_generator.__next__()

    t = torch.from_numpy(cv2.cvtColor(first_frame.img, cv2.COLOR_BGR2RGB))
    # change axes of image loaded image to be compatilbe with torch.io.read_image (which has C,W,H format instead of W,H,C)
    t = t.permute(2, 0, 1)

    # weights =KeypointRCNN_ResNet50_FPN_Weights.DEFAULT
    # model = keypointrcnn_resnet50_fpn(weights=weights, box_score_thresh=0.3)

    model = YOLO('EXPERIMENTS/yolov8x.pt')

    # weights = MaskRCNN_ResNet50_FPN_V2_Weights.COCO_V1
    # model = maskrcnn_resnet50_fpn_v2(weights=weights, box_score_thresh=0.50)
    # model.to(device)
    # # Put the model in inference mode
    # model.eval()

    # Get the transforms for the model's weights
    # preprocess = weights.transforms().to(device)
    # mot_tracker = DeepSort(n_init=1, max_iou_distance=1, max_cosine_distance=0.7, max_age=20, nms_max_overlap=1,
    #                         #   embedder='torchreid', embedder_wts="../MODELS/osnet_x1_0_imagenet.pth"
    #                         )
    
    tracks = collections.defaultdict(lambda: Track())


    for frame in frame_generator:
        # detections: [Detection] = _resnet_track(model, preprocess, mot_tracker, frame.img, scale = 1)
        detections: [Detection] = _yolov8_track(frame, model)
        for detection in detections:
            track = tracks[detection.track_id]
            track.track_id = detection.track_id # for new tracks

            track.history.append(detection)
        
        active_track_ids = [d.track_id for d in detections]
        active_tracks = {t.track_id: t for t in tracks.values() if t.track_id in active_track_ids}
        # logger.info(f"{trajectories}")
        frame.tracks = active_tracks
        yield frame

def _yolov8_track(frame: Frame, model: YOLO) -> [Detection]:
    results: [YOLOResult] = model.track(frame.img, persist=True, tracker="bytetrack.yaml", verbose=False)
    if results[0].boxes is None or results[0].boxes.id is None:
        # work around https://github.com/ultralytics/ultralytics/issues/5968
        return []
    return [Detection(track_id, bbox[0]-.5*bbox[2], bbox[1]-.5*bbox[3], bbox[2], bbox[3], 1, DetectionState.Confirmed, frame.index) for bbox, track_id in zip(results[0].boxes.xywh.cpu(), results[0].boxes.id.int().cpu().tolist())]

def _resnet_track(model, preprocess, mot_tracker: DeepSort, img, scale: float = 1) -> [Detection]:
    if scale != 1:
        dsize = (int(img.shape[1] * scale), int(img.shape[0] * scale))
        img = cv2.resize(img, dsize)
    detections = _resnet_detect_persons(model, preprocess, img)
    tracks: [DeepsortTrack] = mot_tracker.update_tracks(detections, frame=img)
    return [Detection.from_deepsort(t).get_scaled(1/scale) for t in tracks]

def _resnet_detect_persons(model, preprocess, frame) -> [Detection]:
    t = torch.from_numpy(cv2.cvtColor(frame, cv2.COLOR_BGR2RGB))
    # change axes of image loaded image to be compatilbe with torch.io.read_image (which has C,W,H format instead of W,H,C)
    t = t.permute(2, 0, 1)

    batch = preprocess(t)[None, :].to(device)
    # no_grad can be used on inference, should be slightly faster
    with torch.no_grad():
        predictions = model(batch)
    prediction = predictions[0] # we feed only one frame at once

    # TODO: check if we need e.g. cyclist
    mask = prediction['labels'] == 1 # if we want more than one label: np.isin(prediction['labels'], [1,86])

    scores = prediction['scores'][mask]
    labels = prediction['labels'][mask]
    boxes = prediction['boxes'][mask]
    
    # TODO: introduce confidence and NMS supression: https://github.com/cfotache/pytorch_objectdetecttrack/blob/master/PyTorch_Object_Tracking.ipynb
    # (which I _think_ we better do after filtering)
    # alternatively look at Soft-NMS https://towardsdatascience.com/non-maximum-suppression-nms-93ce178e177c

    #  dets - a numpy array of detections in the format [[x1,y1,x2,y2,score, label],[x1,y1,x2,y2,score, label],...]
    detections = np.array([np.append(bbox, [score, label]) for bbox, score, label in zip(boxes.cpu(), scores.cpu(), labels.cpu())])
    detections = detect_persons_deepsort_wrapper(detections)
    
    return detections

def detect_persons_deepsort_wrapper(detections):
    """make detect_persons() compatible with
    deep_sort_realtime tracker by going from ltrb to ltwh and
    different nesting
    """
    return [([d[0], d[1], d[2]-d[0], d[3]-d[1]], d[4], d[5]) for d in detections]


In [5]:
from tsmoothie.smoother import KalmanSmoother, ConvolutionSmoother

def smooth_detections(frame_generator: collections.abc.Iterable[Frame]):
    smoother = ConvolutionSmoother(window_len=2, window_type='ones', copy=None)
    # smoother = KalmanSmoother(component='level_trend', 
    #                         component_noise={'level':0.01, 'trend':0.01})

    for frame in frame_generator:
        new_tracks = []
        for track in frame.tracks.values():
            ls = [d.l for d in track.history]
            ts = [d.t for d in track.history]
            ws = [d.w for d in track.history]
            hs = [d.h for d in track.history]
            smoother.smooth(ls)
            ls = smoother.smooth_data[0]
            smoother.smooth(ts)
            ts = smoother.smooth_data[0]
            smoother.smooth(ws)
            ws = smoother.smooth_data[0]
            smoother.smooth(hs)
            hs = smoother.smooth_data[0]
            new_history = [Detection(d.track_id, l, t, w, h, d.conf, d.state, d.frame_nr) for l, t, w, h, d in zip(ls,ts,ws,hs, track.history)]
            new_track = Track(track.track_id, new_history, track.predictor_history, track.predictions)
            new_tracks.append(new_track)
        frame.tracks = {t.track_id: t for t in new_tracks}
        yield frame


In [6]:
import csv

#TODO _afmaken_, schrijf pas in de achteraf vanwege smoothing? NEE, store voor smoothen, maar OOK frame_index in detection
def store_tracks_for_training(frame_generator: Iterable[Frame]):
    tracks = {}
    
    try:
        for frame in frame_generator:
            if frame.tracks:
                for track_id, track in frame.tracks.items():
                    tracks[track_id] = track
            yield frame
            
    except KeyboardInterrupt as e:
        print("stopped with keyboard")
    finally:
        print('Write file')
        with open("EXPERIMENTS/test_track.csv", 'w') as fp:
            training_csv = csv.DictWriter(fp, fieldnames=['frame_id', 'track_id', 'l', 't', 'w', 'h', 'x', 'y', 'state'], delimiter='\t', quoting=csv.QUOTE_NONE)
            for track in tracks.values():
                training_csv.writerows([{
                            'frame_id': round(detection.frame_nr * 10., 1), # not really time
                            'track_id': track.track_id,
                            'l': detection.l,
                            't': detection.t,
                            'w': detection.w,
                            'h': detection.h,
                            'x': projected_detection[0],
                            'y': projected_detection[1],
                            'state': detection.state.value
                            # only keep _actual_detections, no lost entries
                            } for detection, projected_detection in zip(track.history, track.get_projected_history(frame.H))
                            # if t.history[-1].state != DetectionState.Lost
                            ])

In [7]:

import ffmpeg

from trap.renderer import decorate_frame

def streamer(frame_generator: collections.abc.Iterable[Frame]):
    render_url = "zmq:tcp://0.0.0.0:5556"
    frame_size = (1280,720)
    streaming_process = start_streaming(frame_size, render_url, 25)
    first_time = None
    try:
        for frame in frame_generator:
            if not first_time:
                first_time = frame.time
            # img = frame.img
            img = decorate_frame(frame, frame,first_time)
            streaming_process.stdin.write(img.tobytes())
            yield frame
    finally:
        streaming_process.stdin.close()
        streaming_process.wait()

def start_streaming(frame_size, render_url, fps):
        return (
            ffmpeg
            .input('pipe:', format='rawvideo',codec="rawvideo", pix_fmt='bgr24', s='{}x{}'.format(*frame_size))
            .output(
                render_url,
                #codec = "copy", # use same codecs of the original video
                codec='libx264',
                listen=1, # enables HTTP server
                pix_fmt="yuv420p",
                preset="ultrafast",
                tune="zerolatency",
                g=f"{fps*2}",
                analyzeduration="2000000",
                probesize="1000000",
                f='mpegts'
            )
            .overwrite_output()
            .run_async(pipe_stdin=True)
        )

In [8]:
def frame_generator(video_srcs: [Path]) -> collections.abc.Iterable[Frame]:
    i = 0
    for video_path in video_srcs:
        print(video_path)
        video = cv2.VideoCapture(str(video_path))
        fps = video.get(cv2.CAP_PROP_FPS)

        duration = video.get(cv2.CAP_PROP_FRAME_COUNT)

        # start = video.set(cv2.CAP_PROP_POS_FRAMES, 1900+45000)

        if '-' in video_path.stem:
            path_stem = video_path.stem[:video_path.stem.rfind('-')]
        else:
            path_stem = video_path.stem
        path_stem += "-homography"
        homography_path = video_path.with_stem(path_stem).with_suffix('.txt')
        print(f'check homography file {homography_path}')

        if homography_path.exists():
            print(f'Found custom homography file! Using {homography_path}')
            video_H = np.loadtxt(homography_path, delimiter=',')
        else:
            video_H = None

        # pbar = tqdm(total=duration)
        while True:
            # pbar.update(1)
            ret, img = video.read()

            # seek to 0 if video has finished. Infinite loop
            if not ret:
                # now loading multiple files        
                # TODO trigger detector reset
                break
                
            
            if "DATASETS/hof/" in str(video_path):
                # hack to mask out area
                cv2.rectangle(img, (0,0), (800,200), (0,0,0), -1)

            frame = Frame(index=i, img=img, H=video_H)
            i += 1
            yield frame


In [9]:
from IPython.display import display, Markdown

In [10]:
display(Markdown("view stream with `ffplay zmq:tcp://100.109.175.82:5556`"))
for detections in tqdm(streamer(store_tracks_for_training(smooth_detections(tracker(frame_generator(video_srcs)))))):
# for detections in tqdm(store_tracks_for_training(smooth_detections(tracker(frame_generator(video_srcs))))):
# for frame in frame_generator(video_srcs):
    # print(detections)
    pass
    # if len(detections):
    #     print(detections)
    #     break

    # break


view stream with `ffplay zmq:tcp://100.109.175.82:5556`

0it [00:00, ?it/s]ffmpeg version 5.1.4-0+deb12u1 Copyright (c) 2000-2023 the FFmpeg developers
  built with gcc 12 (Debian 12.2.0-14)
  configuration: --prefix=/usr --extra-version=0+deb12u1 --toolchain=hardened --libdir=/usr/lib/x86_64-linux-gnu --incdir=/usr/include/x86_64-linux-gnu --arch=amd64 --enable-gpl --disable-stripping --enable-gnutls --enable-ladspa --enable-libaom --enable-libass --enable-libbluray --enable-libbs2b --enable-libcaca --enable-libcdio --enable-libcodec2 --enable-libdav1d --enable-libflite --enable-libfontconfig --enable-libfreetype --enable-libfribidi --enable-libglslang --enable-libgme --enable-libgsm --enable-libjack --enable-libmp3lame --enable-libmysofa --enable-libopenjpeg --enable-libopenmpt --enable-libopus --enable-libpulse --enable-librabbitmq --enable-librist --enable-librubberband --enable-libshine --enable-libsnappy --enable-libsoxr --enable-libspeex --enable-libsrt --enable-libssh --enable-libsvtav1 --enable-libtheora --enable-libtwolame --enable

../DATASETS/hof/webcam20240110-4.m4v
check homography file ../DATASETS/hof/webcam20240110-homography.txt
Found custom homography file! Using ../DATASETS/hof/webcam20240110-homography.txt


/home/ruben/suspicion/trap/.venv/lib/python3.10/site-packages/numpy/lib/function_base.py:520: RuntimeWarning: Mean of empty slice.
  avg = a.mean(axis, **keepdims_kw)
/home/ruben/suspicion/trap/.venv/lib/python3.10/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
1it [00:02,  2.89s/it]Input #0, rawvideo, from 'pipe:':
  Duration: N/A, start: 0.000000, bitrate: 552960 kb/s
  Stream #0:0: Video: rawvideo (BGR[24] / 0x18524742), bgr24, 1280x720, 552960 kb/s, 25 tbr, 25 tbn
Stream mapping:
  Stream #0:0 -> #0:0 (rawvideo (native) -> h264 (libx264))
[libx264 @ 0x5597952eb880] using cpu capabilities: MMX2 SSE2Fast SSSE3 SSE4.2 AVX FMA3 BMI2 AVX2
[libx264 @ 0x5597952eb880] profile Constrained Baseline, level 3.1, 4:2:0, 8-bit
Output #0, mpegts, to 'zmq:tcp://0.0.0.0:5556':
  Metadata:
    encoder         : Lavf59.27.100
  Stream #0:0: Video: h264, yuv420p(tv, progressive), 1280x720, q=2-31, 25 fps, 90k tb

33931it [10:15, 52.82it/s]ame=  218 fps= 62 q=14.0 size=    1891kB time=00:00:08.68 bitrate=1784.7kbits/s speed=2.45x    frame=  249 fps= 61 q=13.0 size=    1967kB time=00:00:09.92 bitrate=1624.5kbits/s speed=2.45x    frame=  280 fps= 61 q=14.0 size=    2309kB time=00:00:11.16 bitrate=1694.7kbits/s speed=2.45x    frame=  311 fps= 61 q=17.0 size=    2692kB time=00:00:12.40 bitrate=1778.2kbits/s speed=2.44x    frame=  343 fps= 61 q=13.0 size=    2822kB time=00:00:13.68 bitrate=1690.0kbits/s speed=2.45x    frame=  374 fps= 61 q=13.0 size=    3143kB time=00:00:14.92 bitrate=1725.7kbits/s speed=2.45x    frame=  405 fps= 61 q=17.0 size=    3507kB time=00:00:16.16 bitrate=1777.9kbits/s speed=2.45x    frame=  437 fps= 61 q=14.0 size=    3589kB time=00:00:17.44 bitrate=1685.6kbits/s speed=2.45x    frame=  468 fps= 61 q=13.0 size=    3916kB time=00:00:18.68 bitrate=1717.5kbits/s speed=2.45x    frame=  499 fps= 61 q=13.0 size=    3984kB time=00:00:19.92 bitrate=1638.4kbits/s speed=2.45x    frame=

...

264995it [1:16:49, 52.86it/s]ize= 2292245kB time=02:37:43.68 bitrate=1984.2kbits/s speed=2.29x    frame=236623 fps= 57 q=14.0 size= 2292552kB time=02:37:44.88 bitrate=1984.2kbits/s speed=2.29x    frame=236653 fps= 57 q=21.0 size= 2292844kB time=02:37:46.08 bitrate=1984.2kbits/s speed=2.29x    frame=236682 fps= 57 q=13.0 size= 2292898kB time=02:37:47.24 bitrate=1984.0kbits/s speed=2.29x    frame=236712 fps= 57 q=13.0 size= 2293303kB time=02:37:48.44 bitrate=1984.1kbits/s speed=2.29x    frame=236742 fps= 57 q=13.0 size= 2293343kB time=02:37:49.64 bitrate=1983.9kbits/s speed=2.29x    frame=236772 fps= 57 q=13.0 size= 2293624kB time=02:37:50.84 bitrate=1983.9kbits/s speed=2.29x    frame=236802 fps= 57 q=23.0 size= 2293975kB time=02:37:52.04 bitrate=1984.0kbits/s speed=2.29x    frame=236832 fps= 57 q=13.0 size= 2294013kB time=02:37:53.24 bitrate=1983.8kbits/s speed=2.29x    frame=236863 fps= 57 q=13.0 size= 2294297kB time=02:37:54.48 bitrate=1983.7kbits/s speed= 2.3x    frame=236894 fps= 57

../DATASETS/hof/webcam20240111-3.m4v
check homography file ../DATASETS/hof/webcam20240111-homography.txt
Found custom homography file! Using ../DATASETS/hof/webcam20240111-homography.txt


318641it [1:32:55, 58.08it/s]frame=265012 fps= 58 q=14.0 size= 2485264kB time=02:56:40.44 bitrate=1920.6kbits/s speed= 2.3x    frame=265043 fps= 58 q=13.0 size= 2485347kB time=02:56:41.68 bitrate=1920.4kbits/s speed= 2.3x    frame=265074 fps= 58 q=13.0 size= 2485753kB time=02:56:42.92 bitrate=1920.5kbits/s speed= 2.3x    frame=265104 fps= 58 q=20.0 size= 2486402kB time=02:56:44.12 bitrate=1920.8kbits/s speed= 2.3x    frame=265134 fps= 58 q=13.0 size= 2486446kB time=02:56:45.32 bitrate=1920.6kbits/s speed= 2.3x    frame=265164 fps= 58 q=13.0 size= 2486881kB time=02:56:46.52 bitrate=1920.8kbits/s speed= 2.3x    frame=265194 fps= 58 q=14.0 size= 2487038kB time=02:56:47.72 bitrate=1920.7kbits/s speed= 2.3x    frame=265224 fps= 58 q=15.0 size= 2487516kB time=02:56:48.92 bitrate=1920.8kbits/s speed= 2.3x    frame=265252 fps= 58 q=25.0 size= 2488019kB time=02:56:50.04 bitrate=1921.0kbits/s speed= 2.3x    frame=265280 fps= 58 q=16.0 size= 2488182kB time=02:56:51.16 bitrate=1920.9kbits/s speed=

Write file


frame=318643 fps= 57 q=15.0 Lsize= 3156297kB time=03:32:25.68 bitrate=2028.6kbits/s speed=2.29x    
video:3009973kB audio:0kB subtitle:0kB other streams:0kB global headers:0kB muxing overhead: 4.861295%
[libx264 @ 0x5597952eb880] frame I:6373  Avg QP:11.64  size:288292
[libx264 @ 0x5597952eb880] frame P:312270 Avg QP:14.95  size:  3987
[libx264 @ 0x5597952eb880] mb I  I16..4: 100.0%  0.0%  0.0%
[libx264 @ 0x5597952eb880] mb P  I16..4:  0.1%  0.0%  0.0%  P16..4: 13.7%  0.0%  0.0%  0.0%  0.0%    skip:86.2%
[libx264 @ 0x5597952eb880] coded y,uvDC,uvAC intra: 84.6% 81.4% 73.8% inter: 4.0% 7.6% 0.8%
[libx264 @ 0x5597952eb880] i16 v,h,dc,p: 22% 25% 41% 12%
[libx264 @ 0x5597952eb880] i8c dc,h,v,p: 54% 23% 14%  9%
[libx264 @ 0x5597952eb880] kb/s:1934.59
318643it [1:32:56, 57.14it/s]
